In [1]:
import torch
import sys
sys.path.append('/lustre/project/Stat/s1155202250/fastfolder/code/st/istar')

In [2]:
from impute import *

/stat_Lin_Group/s1155202250/basic/conda/envs/pytorchlin/lib/python3.9/site-packages/scipy/__init__.py:155: UserWarning: A NumPy version >=1.18.5 and <1.25.0 is required for this version of SciPy (detected version 1.26.4
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"


In [3]:
import argparse

class Args:
    def __init__(self, prefix, epochs=None, n_states=5, device='cuda', n_jobs=1, load_saved=False):
        self.prefix = prefix
        self.epochs = epochs
        self.n_states = n_states
        self.device = device
        self.n_jobs = n_jobs
        self.load_saved = load_saved


In [4]:
prefix='/lustre/project/Stat/s1155202250/fastfolder/code/st/istar/data/10xdata/Xenium_FFPE_Human_Breast_Cancer_Rep1/istar_/'  # e.g. data/demo/

device="cuda:1"  # "cuda" or "cpu"
pixel_size=0.5  # desired pixel size for the whole analysis
n_genes=313  # number of most variable genes to impute


In [5]:
args=Args(prefix, epochs=100, n_states=5, device=device, n_jobs=1, load_saved=False)

In [6]:
embs, cnts, locs = get_data(args.prefix)

Dataframe loaded from /lustre/project/Stat/s1155202250/fastfolder/code/st/istar/data/10xdata/Xenium_FFPE_Human_Breast_Cancer_Rep1/istar_/cnts.tsv
Pickle loaded from /lustre/project/Stat/s1155202250/fastfolder/code/st/istar/data/10xdata/Xenium_FFPE_Human_Breast_Cancer_Rep1/istar_/embeddings-hist.pickle
Dataframe loaded from /lustre/project/Stat/s1155202250/fastfolder/code/st/istar/data/10xdata/Xenium_FFPE_Human_Breast_Cancer_Rep1/istar_/locs.tsv
Image loaded from /lustre/project/Stat/s1155202250/fastfolder/code/st/istar/data/10xdata/Xenium_FFPE_Human_Breast_Cancer_Rep1/istar_/he.jpg


In [7]:
embs.shape

(768, 976, 579)

In [ ]:

factor = 16
radius = int(read_string(f'{args.prefix}radius.txt'))
radius = radius / factor

n_train = cnts.shape[0]
batch_size = min(128, n_train//16)


In [ ]:
names = cnts.columns
cnts = cnts.to_numpy()
cnts = cnts.astype(np.float32)

__, cnts, __, (cnts_min, cnts_max) = normalize(embs, cnts)



In [ ]:

epochs=args.epochs
n_states=args.n_states
prefix=args.prefix
load_saved=args.load_saved
device=args.device
n_jobs=args.n_jobs

In [ ]:
kwargs_list = [
        dict(
            x=embs, y=cnts, locs=locs, radius=radius,
            batch_size=batch_size, epochs=epochs, lr=1e-4,
            prefix=f'{prefix}states/{i:02d}/',
            load_saved=load_saved, device=device)
        for i in range(n_states)]


In [ ]:
n_states

5

In [ ]:
#  if n_jobs == 1:
#         out_list = [get_model_kwargs(kwargs) for kwargs in kwargs_list]

In [ ]:
kwargs=kwargs_list[0]


In [ ]:
x=kwargs['x']
y=kwargs['y']
locs=kwargs['locs']
radius=kwargs['radius']
batch_size=kwargs['batch_size']
epochs=kwargs['epochs']
lr=kwargs['lr']
prefix=kwargs['prefix']
load_saved=kwargs['load_saved']
device=kwargs['device']

In [ ]:
print('x:', x.shape, ', y:', y.shape)

x: (768, 976, 579) , y: (167780, 313)


In [ ]:
locs

array([[ 10,  26],
       [ 10,  26],
       [ 10,  26],
       ...,
       [160, 233],
       [160, 234],
       [160, 234]])

In [ ]:
dataset = SpotDataset(x, y, locs, radius)

In [ ]:
batch=next(iter(dataset))


In [ ]:
batch[0].shape

(121, 579)

In [ ]:
batch[1].shape

(313,)

In [ ]:
class SpotDataset2(Dataset):

    def __init__(self, x_all, y, locs, radius):
        super().__init__()
        mask = get_disk_mask(radius)
        x = get_patches_flat(x_all, locs, mask)
        isin = np.isfinite(x).all((-1, -2))
        self.x = x[isin]
        self.y = y[isin]
        self.locs = locs[isin]
        self.size = x_all.shape[:2]
        self.radius = radius
        self.mask = mask

    def __len__(self):
        return len(self.x)

    def __getitem__(self, idx):
        return self.x[idx], self.y[idx]

    def show(self, channel_x, channel_y, prefix):
        mask = self.mask
        size = self.size
        locs = self.locs
        xs = self.x
        ys = self.y

        plot_spot_masked_image(
                locs=locs, values=xs[:, :, channel_x], mask=mask, size=size,
                outfile=f'{prefix}x{channel_x:04d}.png')

        plot_spot_masked_image(
                locs=locs, values=ys[:, channel_y], mask=mask, size=size,
                outfile=f'{prefix}y{channel_y:04d}.png')


In [ ]:
def get_patches_flat(img, locs, mask):
    shape = np.array(mask.shape)
    center = shape // 2
    r = np.stack([-center, shape-center], -1)  # offset
    x_list = []
    for s in locs:
        patch = img[
            max(s[0]+r[0][0], 0):min(s[0]+r[0][1], img.shape[0]),
            max(s[1]+r[1][0], 0):min(s[1]+r[1][1], img.shape[1])
        ]
        # check patch shape the first two dimensions should be equal to shape
        if patch.shape[:2] != mask.shape:
            # print(s, patch.shape, shape)
            patch = np.full((shape[0], shape[1],img.shape[2]), np.inf)
        if mask.all():
            x = patch
        else:
            x = patch[mask]
            print('after mask')
            print(x.shape)

        x_list.append(x)
    x_list = np.stack(x_list)
    print(x_list.shape)
    return x_list

In [ ]:
mask = get_disk_mask(radius)
x_data = get_patches_flat(x, locs, mask)

after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask
(121, 579)
after mask